In [1]:
require './GenericConvolution.rb'
require './WaveletFilters.rb'
require './MagicFilter.rb'

true

In [2]:
openmp = true
def MagicFilter1d(filter, optims=GenericOptimization::new)
  conv_operation = GenericConvolutionOperator1d::new(filter, :ld => true, :narr => true, :a_x => true,:a_y=>true, :a => true)
  conv_operation.optimize(optims) if optims

  p, subops = conv_operation.procedure

  kernel = BOAST::CKernel::new

  print_header

  subops.each_value { |op|
    BOAST::pr op
    puts "chosen:"+ op.name
  }
  BOAST::pr p

  kernel.procedure = p
  kernel.cost_function = lambda { |*args| conv_operation.cost(*args) }
  return kernel
end

:MagicFilter1d

In [4]:
n1 = 32
n2 = 32
n3 = 32
optims = GenericOptimization::new(:repeat => 9, :unroll_range => [8,8], :mod_arr_test => true, :tt_arr_test => true, :dimensions => [n1,n2,n3], :vector_length => [2,4], :unrolled_dim_index_test => true, :openmp => openmp)
conv_filter = ConvolutionFilter::new('sym8_md',SYM8_MF.reverse,8)
5

5

In [5]:
ksym8 = MagicFilter1d( conv_filter, optims )

d_sym8_md_p_10_ld_u8_v1_1_t_t_t: 0.043362000000000005 ms 24.18191042848577 GFlops
d_sym8_md_p_10_ld_u8_v1_1_t_f_t: 0.032293 ms 32.470690242467406 GFlops
d_sym8_md_p_10_ld_u8_v1_1_f_t_t: 0.055060000000000005 ms 19.04424264438794 GFlops
d_sym8_md_p_10_ld_u8_v1_1_f_f_t: 0.060375000000000005 ms 17.367718426501032 GFlops
d_sym8_md_p_10_a_ld_u8_v1_1_t_t_t: 0.044477 ms 23.57569080648425 GFlops
d_sym8_md_p_10_a_ld_u8_v1_1_t_f_t: 0.032744 ms 32.02345467871976 GFlops
d_sym8_md_p_10_a_ld_u8_v1_1_f_t_t: 0.056802000000000005 ms 18.4601950635541 GFlops
d_sym8_md_p_10_a_ld_u8_v1_1_f_f_t: 0.060943000000000004 ms 17.205848087557225 GFlops
d_sym8_md_p_10_ain_ld_u8_v1_1_t_t_t: 0.054271 ms 19.321110722116785 GFlops
d_sym8_md_p_10_ain_ld_u8_v1_1_t_f_t: 0.034424 ms 30.460608877527307 GFlops
d_sym8_md_p_10_ain_ld_u8_v1_1_f_t_t: 0.064775 ms 16.18797375530683 GFlops
d_sym8_md_p_10_ain_ld_u8_v1_1_f_f_t: 0.062547 ms 16.764609014021453 GFlops
d_sym8_md_p_10_ay_ld_u8_v1_1_t_t_t: 0.048969000000000006 ms 21.41305724

SUBROUTINE d_sym8_md_p_10_ld_u8_v1_1_t_f_t(n, ndat, nx, ny, x, y)
  integer, parameter :: wp=kind(1.0d0)
  integer(kind=4), parameter :: lowfil = -8
  integer(kind=4), parameter :: upfil = 7
  integer(kind=4), intent(in) :: n
  integer(kind=4), intent(in) :: ndat
  integer(kind=4), intent(in) :: nx
  integer(kind=4), intent(in) :: ny
  real(kind=8), intent(in), dimension(0:nx - (1), 0:ndat - (1)) :: x
  real(kind=8), intent(out), dimension(0:ny - (1), 0:ndat - (1)) :: y
  real(kind=8), parameter, dimension(-8:7) :: sym8_md_fil = reshape((/&
& &
8.4334247333529341094733325815816232969177478728797427310317e-7_wp, &
-0.00001290557201342060969516786758559028264129757158423127355882943e0&
&_wp, &
0.000087629844762105595646891618941163970464425424613649618138794e0_wp&
&, &
-0.000301580381326904631671637038261698791032841826554967601640246e0_w&
&p, &
0.001747237136729939034494478127498529416920979083511241686685502e0_wp&
&, &
-0.00942047030201080385922711540948195074607340327611386232053071e0

In [6]:
input = ANArray.float(64,n1,n2,n3).random!
work1 = ANArray.float(64,n1,n2,n3)
work2 = ANArray.float(64,n1,n2,n3)
output = ANArray.float(64,n1,n2,n3)
output_ref = ANArray.float(64,n1,n2,n3)
epsilon = 10e-15

1.0e-14

In [8]:
k_ref = magicfilter_ref
stats = k_ref.run(n1, n2*n3, input, output_ref)
stats = k_ref.run(n2, n1*n3, output_ref, work1)
stats = k_ref.run(n3, n2*n1, work1, output_ref)
k_ref.dump_source

In [9]:
n = NArray.int(3)
n[0] = n1
n[1] = n2
n[2] = n3

32

In [10]:
ksym8.build(:openmp => openmp)

SUBROUTINE d_sym8_md_p_10_ld_u8_v1_1_t_f_t(n, ndat, nx, ny, x, y)
  integer, parameter :: wp=kind(1.0d0)
  integer(kind=4), parameter :: lowfil = -8
  integer(kind=4), parameter :: upfil = 7
  integer(kind=4), intent(in) :: n
  integer(kind=4), intent(in) :: ndat
  integer(kind=4), intent(in) :: nx
  integer(kind=4), intent(in) :: ny
  real(kind=8), intent(in), dimension(0:nx - (1), 0:ndat - (1)) :: x
  real(kind=8), intent(out), dimension(0:ny - (1), 0:ndat - (1)) :: y
  real(kind=8), parameter, dimension(-8:7) :: sym8_md_fil = reshape((/&
& &
8.4334247333529341094733325815816232969177478728797427310317e-7_wp, &
-0.00001290557201342060969516786758559028264129757158423127355882943e0&
&_wp, &
0.000087629844762105595646891618941163970464425424613649618138794e0_wp&
&, &
-0.000301580381326904631671637038261698791032841826554967601640246e0_w&
&p, &
0.001747237136729939034494478127498529416920979083511241686685502e0_wp&
&, &
-0.00942047030201080385922711540948195074607340327611386232053071e0

In [11]:
ksym8.dump_source
stats0 = ksym8.run(3, 0, n, BC::PERIODIC, n, n, 1, input, work1,1.0,0.0,0.0)
stats0 = ksym8.run(3, 0, n, BC::PERIODIC, n, n, 1, input, work1,1.0,0.0,0.0)
stats1 = ksym8.run(3, 1, n, BC::PERIODIC, n, n, 1, work1, work2,1.0,0.0,0.0)
stats2 = ksym8.run(3, 2, n, BC::PERIODIC, n, n, 1, work2, output,1.0,0.0,0.0)
puts "#{ksym8.procedure.name} d0: #{stats0[:duration]*1.0e3} ms #{32*n1*n2*n3 / (stats0[:duration]*1.0e9)} GFlops"
puts "#{ksym8.procedure.name} d1: #{stats1[:duration]*1.0e3} ms #{32*n1*n2*n3 / (stats1[:duration]*1.0e9)} GFlops"
puts "#{ksym8.procedure.name} d2: #{stats2[:duration]*1.0e3} ms #{32*n1*n2*n3 / (stats2[:duration]*1.0e9)} GFlops"
puts "#{ksym8.procedure.name}: #{(stats0[:duration]+stats1[:duration]+stats2[:duration])*1.0e3} ms #{3*32*n1*n2*n3 / ((stats0[:duration]+stats1[:duration]+stats2[:duration])*1.0e9)} GFlops"
5

d_s0s0_1d_sym8_md d0: 6.780338 ms 0.1546495174724328 GFlops
d_s0s0_1d_sym8_md d1: 6.623858000000001 ms 0.15830291047905917 GFlops
d_s0s0_1d_sym8_md d2: 5.890189 ms 0.17802077318741383 GFlops
d_s0s0_1d_sym8_md: 19.294385000000002 ms 0.16303852131073368 GFlops


5

In [13]:
diff = (output_ref - output).abs
diff.each { |elem|
  raise "Warning: residue too big: #{elem}" if elem > epsilon
}
puts 'ok'

ok


In [14]:
File.open('Magicfilter8.f90','w'){ | f |
  f.write(ksym8.to_s)
  }

1878571